Instalando Pacote

In [1]:
!git clone https://github.com/huggingface/transformers;
!cd transformers; pip3 install .

Cloning into 'transformers'...
remote: Enumerating objects: 159719, done.
remote: Counting objects: 100% (1167/1167), done.
remote: Compressing objects: 100% (711/711), done.
remote: Total 159719 (delta 628), reused 658 (delta 366), pack-reused 158552
Receiving objects: 100% (159719/159719), 161.25 MiB | 16.24 MiB/s, done.
Resolving deltas: 100% (119655/119655), done.
Processing /content/transformers
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 294.9/294.9 kB 5.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.8/3.8 MB 20.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 27.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 268.8/268.8 kB 27.8 MB/s eta 0:00:00
  Created wheel for transformers: filename=transformers-4.34.0.dev0-py3-none-any.whl size=7700260 sha256=9f23ff44b011a74f72fb444fff6c7f9d40fc

In [2]:
! pip install simpletransformers

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 250.8/250.8 kB 4.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 519.6/519.6 kB 9.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.6/43.6 kB 4.5 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 14.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.1/8.1 MB 29.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 40.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 189.5/189.5 kB 17.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 224.8/224.8 kB 23.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.3/115.3 kB 8.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 19.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 10.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

In [3]:
! pip install datasets

Puxando Dataset de Discurso de Ódio

In [4]:
from google.colab import drive
drive.mount('drive')

Mounted at drive


In [5]:
import pandas as pd
import transformers
from transformers import AutoModel, BertTokenizerFast
import torch
import torch.nn as nn
from torch.utils.data import TensorDataset, DataLoader, RandomSampler, SequentialSampler
from transformers import AdamW
import tensorflow as tf
import numpy as np
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from sklearn.metrics import accuracy_score, f1_score
from sklearn.utils.class_weight import compute_class_weight
from sklearn.linear_model import SGDClassifier
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.feature_extraction.text import CountVectorizer



# link: https://huggingface.co/datasets/ag_news

In [6]:
test = pd.read_csv('/content/drive/My Drive/Colab Notebooks/t5_key_text/original/base_ironic_test.csv', sep = ';', decimal = ',')
test.head()

text  label
0  @user Can U Help?||More conservatives needed o...      0
1  Just walked in to #Starbucks and asked for a "...      1
2                                     #NOT GONNA WIN      0
3   @user He is exactly that sort of person. Weirdo!      0
4  So much #sarcasm at work mate 10/10 #boring 10...      1

In [7]:
# X_train = dataset['train']['text']
X_test = test['text']
# y_train = dataset['train']['label']
y_test = test['label']

In [8]:
nclasses = len(np.unique(y_test))

In [9]:
nclasses

2

In [10]:
def puxa_dados_normal(caminho):
  csv = pd.read_csv(caminho, sep = ';', decimal = ',')
  original = csv[['texto', 'label']].copy()
  original = original.drop_duplicates()

  # csv = csv[csv['similiaridade_parafrase'] >= 0.95].copy()


  parafrase = csv[['generated', 'label']].copy()
  parafrase = parafrase.drop_duplicates()
  parafrase = parafrase[~(parafrase['generated'].isnull())].copy()
  parafrase.rename(columns={"generated": "texto"}, inplace = True)

  fim = original.append(parafrase)

  fim = fim.sample(frac=1)

  X = fim['texto'].values
  y = fim['label'].values


  return X, y


In [11]:
def puxa_original(caminho):
  csv = pd.read_csv(caminho, sep = ';', decimal = ',')

  X = csv['texto'].values
  y = csv['label'].values


  return X, y

In [12]:
def puxa_dados_lambada(caminho, original):
  csv = pd.read_csv(caminho, sep = ';', decimal = ',')
  original = pd.read_csv(original, sep = ';', decimal = ',')

  # csv = csv[csv['similiaridade_parafrase'] >= 0.95].copy()


  parafrase = csv[['generated', 'new_label']].copy()
  # parafrase = parafrase.drop_duplicates()
  parafrase = parafrase[~(parafrase['generated'].isnull())].copy()
  parafrase.rename(columns={"generated": "texto", "new_label": "label"}, inplace = True)

  fim = original.append(parafrase)

  fim = fim.sample(frac=1)

  X = fim['texto'].values
  y = fim['label'].values


  return X, y

In [13]:
def puxa_dados_normal_pkl(caminho):
  csv = pd.read_pickle(caminho)
  original = csv[['texto', 'label']].copy()
  original = original.drop_duplicates()

  # csv = csv[csv['similiaridade_parafrase'] >= 0.95].copy()


  parafrase = csv[['generated', 'label']].copy()
  # parafrase = parafrase.drop_duplicates()
  parafrase = parafrase[~(parafrase['generated'].isnull())].copy()
  parafrase.rename(columns={"generated": "texto"}, inplace = True)

  fim = original.append(parafrase)

  fim = fim.sample(frac=1)

  X = fim['texto'].values
  y = fim['label'].values


  return X, y


In [14]:
def puxa_dados_lambada_pkl_filtro(caminho, original, limiar):
  csv = pd.read_pickle(caminho)
  original = pd.read_csv(original, sep = ';', decimal = ',')

  csv = csv[csv['prob_text'] >= limiar].copy()


  parafrase = csv[['generated', 'new_label']].copy()
  parafrase = parafrase.drop_duplicates()
  parafrase = parafrase[~(parafrase['generated'].isnull())].copy()
  parafrase.rename(columns={"generated": "texto", "new_label": "label"}, inplace = True)

  fim = original.append(parafrase)

  fim = fim.sample(frac=1)

  X = fim['texto'].values
  y = fim['label'].values


  return X, y

In [15]:
def desempenho_LSTM(X_train, X_test, y_train, y_test, classes, num_epochs ):


  # vocab_size = 10000
  embedding_dim = 300
  max_length = 128
  trunc_type = 'post'
  padding_type = 'post'
  oov_tok = '<OOV>'

  tokenizer = Tokenizer( oov_token=oov_tok)
  tokenizer.fit_on_texts(X_train)
  word_index = tokenizer.word_index
  vocab_size = len(word_index)+1

  train_sequences = tokenizer.texts_to_sequences(X_train)
  # val_sequences = tokenizer.texts_to_sequences(X_val)

  train_padded = pad_sequences(train_sequences, maxlen=max_length, padding=padding_type, truncating=trunc_type)
  # val_padded = pad_sequences(val_sequences, maxlen=max_length, padding=padding_type, truncating=trunc_type)

  # model = tf.keras.Sequential([
  #   # Camada Embedding (reduzir dimensionalidade)
  #   tf.keras.layers.Embedding(vocab_size, embedding_dim),
  #   # Camada de LSTM bidirecional
  #   tf.keras.layers.LSTM(embedding_dim),
  #   # Camada densa com Relu
  #   tf.keras.layers.Dense(embedding_dim, activation='relu'),
  #   #Camada de saída para as 4 classes
  #   tf.keras.layers.Dense(classes, activation='softmax')
  #   ])
  model = tf.keras.models.Sequential([
        tf.keras.layers.Embedding(input_dim=vocab_size,
                                  mask_zero= True,
                                  output_dim=embedding_dim,
                                  input_length=max_length,
                                  input_shape=(max_length, )),

        tf.keras.layers.Bidirectional(tf.keras.layers.LSTM(32, return_sequences=True)),
        tf.keras.layers.Bidirectional(tf.keras.layers.LSTM(32, return_sequences=False)),
        tf.keras.layers.Dense(64, activation='relu'),
        tf.keras.layers.Dropout(0.5),
        tf.keras.layers.Dense(units=classes, activation='softmax')
    ])
  # model = tf.keras.Sequential()
  # model.add(tf.keras.layers.Embedding(vocab_size, embedding_dim))
  # model.add(tf.keras.layers.Conv1D(filters=32, kernel_size=3, padding='same', activation='relu'))
  # model.add(tf.keras.layers.MaxPooling1D(pool_size=2))
  # model.add(tf.keras.layers.LSTM(100))
  # model.add(tf.keras.layers.Dense(classes, activation='softmax'))

  model.compile(loss='sparse_categorical_crossentropy', optimizer='adam', metrics=['accuracy'])


  history = model.fit(train_padded, y_train, epochs=num_epochs, verbose=2)

  test_sequences = tokenizer.texts_to_sequences(X_test)
  test_padded = pad_sequences(test_sequences, maxlen=max_length, padding=padding_type, truncating=trunc_type)


  preds_log = model.predict(test_padded)
  preds = tf.argmax(preds_log, 1)
  acc = accuracy_score(y_test, preds)
  f1 = f1_score(y_test, preds, average='macro')

  return acc, f1







In [16]:
def desempenho_CNN(X_train, X_test, y_train, y_test, classes, num_epochs ):


  # vocab_size = 10000
  embedding_dim = 300
  max_length = 128
  trunc_type = 'post'
  padding_type = 'post'
  oov_tok = '<OOV>'

  tokenizer = Tokenizer( oov_token=oov_tok)
  tokenizer.fit_on_texts(X_train)
  word_index = tokenizer.word_index
  vocab_size = len(word_index)+1

  train_sequences = tokenizer.texts_to_sequences(X_train)
  # val_sequences = tokenizer.texts_to_sequences(X_val)

  train_padded = pad_sequences(train_sequences, maxlen=max_length, padding=padding_type, truncating=trunc_type)
  # val_padded = pad_sequences(val_sequences, maxlen=max_length, padding=padding_type, truncating=trunc_type)

  # model = tf.keras.Sequential([
  #   # Camada Embedding (reduzir dimensionalidade)
  #   tf.keras.layers.Embedding(vocab_size, embedding_dim),
  #   # Camada de LSTM bidirecional
  #   tf.keras.layers.LSTM(embedding_dim),
  #   # Camada densa com Relu
  #   tf.keras.layers.Dense(embedding_dim, activation='relu'),
  #   #Camada de saída para as 4 classes
  #   tf.keras.layers.Dense(classes, activation='softmax')
  #   ])
  model = tf.keras.models.Sequential([
        tf.keras.layers.Embedding(input_dim=vocab_size,
                                  mask_zero= True,
                                  output_dim=embedding_dim,
                                  input_length=max_length,
                                  input_shape=(max_length, )),

        tf.keras.layers.Conv1D(filters=100, kernel_size = 3, activation = 'relu',
                               # set 'axis' value to the first and second axis of conv1D weights (rows, cols)
                               kernel_constraint= MaxNorm( max_value=3, axis=[0,1])),

        tf.keras.layers.MaxPool1D(2),
        tf.keras.layers.Flatten(),
        tf.keras.layers.Dropout(0.5),
        tf.keras.layers.Dense(10, activation='relu',
                              # set axis to 0 to constrain each weight vector of length (input_dim,) in dense layer
                              kernel_constraint = MaxNorm( max_value=3, axis=0)),
        tf.keras.layers.Dropout(0.5),
        tf.keras.layers.Dense(units=classes, activation='softmax')
    ])
  # model = tf.keras.Sequential()
  # model.add(tf.keras.layers.Embedding(vocab_size, embedding_dim))
  # model.add(tf.keras.layers.Conv1D(filters=32, kernel_size=3, padding='same', activation='relu'))
  # model.add(tf.keras.layers.MaxPooling1D(pool_size=2))
  # model.add(tf.keras.layers.LSTM(100))
  # model.add(tf.keras.layers.Dense(classes, activation='softmax'))

  model.compile(loss='sparse_categorical_crossentropy', optimizer='adam', metrics=['accuracy'])


  history = model.fit(train_padded, y_train, epochs=num_epochs, verbose=2)

  test_sequences = tokenizer.texts_to_sequences(X_test)
  test_padded = pad_sequences(test_sequences, maxlen=max_length, padding=padding_type, truncating=trunc_type)


  preds_log = model.predict(test_padded)
  preds = tf.argmax(preds_log, 1)
  acc = accuracy_score(y_test, preds)
  f1 = f1_score(y_test, preds, average='macro')

  return acc, f1







In [17]:
# Evaluate the model
from sklearn.metrics import f1_score, accuracy_score

def f1_multiclass(labels, preds):
      return f1_score(labels, preds, average='macro')


In [18]:
def desempenho_transformers(X_train, X_test, y_train, y_test,classes, model,type_model, epochs, batch, max_len):
  from simpletransformers.classification import ClassificationModel
  import pandas as pd
  import logging
  import sklearn

  train_df = pd.DataFrame(X_train)
  train_df['target'] = y_train

  eval_df = pd.DataFrame(X_test)
  eval_df['target'] = y_test



  # Create a ClassificationModel
  model = ClassificationModel(type_model, model, num_labels=classes, args={'num_train_epochs':epochs,
                                                                           'train_batch_size':batch,
                                                                           'max_seq_length':max_len,
                                                                          #  "fp16":False,
                                                                           'overwrite_output_dir': True})

  # Train the model
  model.train_model(train_df)
  result, model_outputs, wrong_predictions = model.eval_model(eval_df, acc=sklearn.metrics.accuracy_score,f1=f1_multiclass)

  return result['acc'], result['f1']





In [19]:

y_test = np.array(y_test)


# Original

In [ ]:
perc = 5
i=0
from tensorflow.keras import regularizers
from tensorflow.keras.constraints import MaxNorm
arqs = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/base_ironic_'+str(perc)+'_original'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/base_ironic_'+str(perc)+'_original'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/base_ironic_'+str(perc)+'_original'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/base_ironic_'+str(perc)+'_original'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/base_ironic_'+str(perc)+'_original'+str(i+5)+'.csv',
       ]

cnn_acc = []
cnn_f1 = []
lstm_acc = []
lstm_f1 = []
bert_acc = []
bert_f1 = []
xlnet_acc = []
xlnet_f1 = []
roberta_acc = []
roberta_f1 = []
import gc
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
torch.cuda.empty_cache()
gc.collect()
for j in range(len(arqs)):
  print(j)
  X_train,  y_train = puxa_original(arqs[j])
  # svm = desempenho_CNN(X_train,  X_test, y_train,  y_test, nclasses, 15)
  # print('CNN')
  # print('ACC:' + str(svm[0]))
  # print('F1:' + str(svm[1]))
  # lstm = desempenho_LSTM(X_train,  X_test, y_train,  y_test, nclasses, 5)
  # print('LSTM')
  # print('ACC:' + str(lstm[0]))
  # print('F1:' + str(lstm[1]))
  # torch.cuda.empty_cache()
  # gc.collect()
  bert = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'bert-base-uncased','bert', 4, 32, 64)

  print('BERT')
  print('ACC:' + str(bert[0]))
  print('F1:' + str(bert[1]))

  torch.cuda.empty_cache()
  gc.collect()

  xlnet = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'xlnet-base-cased','xlnet',  4, 32, 64)
  print('XlNet')
  print('ACC:' + str(xlnet[0]))
  print('F1:' + str(xlnet[1]))

  torch.cuda.empty_cache()
  gc.collect()

  roberta = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'roberta-base','roberta',  4, 32, 64)
  print('Roberta')
  print('ACC:' + str(roberta[0]))
  print('F1:' + str(roberta[1]))

  # cnn_acc.append(svm[0])
  # cnn_f1.append(svm[1])

  # lstm_acc.append(lstm[0])
  # lstm_f1.append(lstm[1])

  bert_acc.append(bert[0])
  bert_f1.append(bert[1])

  xlnet_acc.append(xlnet[0])
  xlnet_f1.append(xlnet[1])

  roberta_acc.append(roberta[0])
  roberta_f1.append(roberta[1])

0


Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:612: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/144 [00:00<?, ?it/s]

Epoch:   0%|          | 0/4 [00:00<?, ?it/s]

...

Running Epoch 3 of 4:   0%|          | 0/5 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1454: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/784 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/98 [00:00<?, ?it/s]

Roberta
ACC:0.6007653061224489
F1:0.5166851477270265


In [ ]:
data = {'Aug': [ 'original1', 'original2', 'original3', 'original4','original5'],
      #  'CNN_ACC': cnn_acc, 'CNN_F1':cnn_f1,
      #   'LSTM_ACC': lstm_acc, 'LSTM_F1':lstm_f1,
        'BERT_ACC': bert_acc, 'BERT_F1':bert_f1,
        'XLNET_ACC': xlnet_acc, 'XLNET_F1':xlnet_f1,
        'ROBERTA_ACC': roberta_acc, 'ROBERTA_F1':roberta_f1,}



base_resultados = pd.DataFrame.from_dict(data)

In [ ]:
base_resultados

Aug  BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
0  original1  0.505102  0.488801   0.547194  0.539241     0.459184    0.407281
1  original2  0.621173  0.619688   0.573980  0.473859     0.619898    0.494911
2  original3  0.547194  0.539857   0.455357  0.408344     0.608418    0.608081
3  original4  0.576531  0.526870   0.551020  0.547202     0.594388    0.529060
4  original5  0.561224  0.559838   0.586735  0.569240     0.600765    0.516685

In [ ]:
base_resultados.describe()

BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
count  5.000000  5.000000   5.000000  5.000000     5.000000    5.000000
mean   0.562245  0.547011   0.542857  0.507577     0.576531    0.511203
std    0.042337  0.048197   0.051564  0.065877     0.066284    0.072110
min    0.505102  0.488801   0.455357  0.408344     0.459184    0.407281
25%    0.547194  0.526870   0.547194  0.473859     0.594388    0.494911
50%    0.561224  0.539857   0.551020  0.539241     0.600765    0.516685
75%    0.576531  0.559838   0.573980  0.547202     0.608418    0.529060
max    0.621173  0.619688   0.586735  0.569240     0.619898    0.608081

# EDA

In [20]:
perc = 5
i=0
from tensorflow.keras import regularizers
from tensorflow.keras.constraints import MaxNorm
arqs = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/eda/base_ironic_'+str(perc)+'_eda'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/eda/base_ironic_'+str(perc)+'_eda'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/eda/base_ironic_'+str(perc)+'_eda'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/eda/base_ironic_'+str(perc)+'_eda'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/eda/base_ironic_'+str(perc)+'_eda'+str(i+5)+'.csv',
       ]

cnn_acc = []
cnn_f1 = []
lstm_acc = []
lstm_f1 = []
bert_acc = []
bert_f1 = []
xlnet_acc = []
xlnet_f1 = []
roberta_acc = []
roberta_f1 = []
import gc
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
torch.cuda.empty_cache()
gc.collect()
for j in range(len(arqs)):
  print(j)
  X_train,  y_train = puxa_dados_normal(arqs[j])
  # svm = desempenho_CNN(X_train,  X_test, y_train,  y_test, nclasses, 15)
  # print('CNN')
  # print('ACC:' + str(svm[0]))
  # print('F1:' + str(svm[1]))
  # lstm = desempenho_LSTM(X_train,  X_test, y_train,  y_test, nclasses, 5)
  # print('LSTM')
  # print('ACC:' + str(lstm[0]))
  # print('F1:' + str(lstm[1]))
  # torch.cuda.empty_cache()
  # gc.collect()
  bert = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'bert-base-uncased','bert', 1, 32, 64)

  print('BERT')
  print('ACC:' + str(bert[0]))
  print('F1:' + str(bert[1]))

  torch.cuda.empty_cache()
  gc.collect()

  xlnet = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'xlnet-base-cased','xlnet',  1, 32, 64)
  print('XlNet')
  print('ACC:' + str(xlnet[0]))
  print('F1:' + str(xlnet[1]))

  torch.cuda.empty_cache()
  gc.collect()

  roberta = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'roberta-base','roberta',  1, 32, 64)
  print('Roberta')
  print('ACC:' + str(roberta[0]))
  print('F1:' + str(roberta[1]))

  # cnn_acc.append(svm[0])
  # cnn_f1.append(svm[1])

  # lstm_acc.append(lstm[0])
  # lstm_f1.append(lstm[1])

  bert_acc.append(bert[0])
  bert_f1.append(bert[1])

  xlnet_acc.append(xlnet[0])
  xlnet_f1.append(xlnet[1])

  roberta_acc.append(roberta[0])
  roberta_f1.append(roberta[1])

0


<ipython-input-10-a91fedf45f9b>:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  fim = original.append(parafrase)


Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Loading the tokenizer from the `special_tokens_map.json` and the `added_tokens.json` will be removed in `transformers 5`,  it is kept for forward compatibility, but it is recommended to update your `tokenizer_config.json` by uploading it again. You will see the new `added_tokens_decoder` attribute that will store the relevant information.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:612: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/719 [00:00<?, ?it/s]

...

Running Epoch 0 of 1:   0%|          | 0/23 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1454: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/784 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/98 [00:00<?, ?it/s]

Roberta
ACC:0.5854591836734694
F1:0.43252555082660177


In [21]:
data = {'Aug': [ 'original1', 'original2', 'original3', 'original4','original5'],
      #  'CNN_ACC': cnn_acc, 'CNN_F1':cnn_f1,
      #   'LSTM_ACC': lstm_acc, 'LSTM_F1':lstm_f1,
        'BERT_ACC': bert_acc, 'BERT_F1':bert_f1,
        'XLNET_ACC': xlnet_acc, 'XLNET_F1':xlnet_f1,
        'ROBERTA_ACC': roberta_acc, 'ROBERTA_F1':roberta_f1,}



base_resultados = pd.DataFrame.from_dict(data)

In [22]:
base_resultados

Aug  BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
0  original1  0.636480  0.636309   0.520408  0.516773     0.521684    0.521028
1  original2  0.568878  0.494922   0.577806  0.559218     0.488520    0.459724
2  original3  0.548469  0.546154   0.539541  0.539504     0.426020    0.337912
3  original4  0.647959  0.643467   0.572704  0.572687     0.482143    0.445320
4  original5  0.522959  0.481375   0.506378  0.488391     0.585459    0.432526

In [23]:
base_resultados.describe()

BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
count  5.000000  5.000000   5.000000  5.000000     5.000000    5.000000
mean   0.584949  0.560445   0.543367  0.535315     0.500765    0.439302
std    0.054903  0.076481   0.031451  0.033657     0.058511    0.066065
min    0.522959  0.481375   0.506378  0.488391     0.426020    0.337912
25%    0.548469  0.494922   0.520408  0.516773     0.482143    0.432526
50%    0.568878  0.546154   0.539541  0.539504     0.488520    0.445320
75%    0.636480  0.636309   0.572704  0.559218     0.521684    0.459724
max    0.647959  0.643467   0.577806  0.572687     0.585459    0.521028

# SSMBA

In [ ]:
perc = 5
i=0
from tensorflow.keras import regularizers
from tensorflow.keras.constraints import MaxNorm
arqs = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/ssmba/base_ironic_'+str(perc)+'_ssmba'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/ssmba/base_ironic_'+str(perc)+'_ssmba'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/ssmba/base_ironic_'+str(perc)+'_ssmba'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/ssmba/base_ironic_'+str(perc)+'_ssmba'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/ssmba/base_ironic_'+str(perc)+'_ssmba'+str(i+5)+'.csv',
       ]

cnn_acc = []
cnn_f1 = []
lstm_acc = []
lstm_f1 = []
bert_acc = []
bert_f1 = []
xlnet_acc = []
xlnet_f1 = []
roberta_acc = []
roberta_f1 = []
import gc
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
torch.cuda.empty_cache()
gc.collect()
for j in range(len(arqs)):
  print(j)
  X_train,  y_train = puxa_dados_normal(arqs[j])
  # svm = desempenho_CNN(X_train,  X_test, y_train,  y_test, nclasses, 15)
  # print('CNN')
  # print('ACC:' + str(svm[0]))
  # print('F1:' + str(svm[1]))
  # lstm = desempenho_LSTM(X_train,  X_test, y_train,  y_test, nclasses, 5)
  # print('LSTM')
  # print('ACC:' + str(lstm[0]))
  # print('F1:' + str(lstm[1]))
  # torch.cuda.empty_cache()
  # gc.collect()
  bert = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'bert-base-uncased','bert', 1, 32, 64)

  print('BERT')
  print('ACC:' + str(bert[0]))
  print('F1:' + str(bert[1]))

  torch.cuda.empty_cache()
  gc.collect()

  xlnet = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'xlnet-base-cased','xlnet',  1, 32, 64)
  print('XlNet')
  print('ACC:' + str(xlnet[0]))
  print('F1:' + str(xlnet[1]))

  torch.cuda.empty_cache()
  gc.collect()

  roberta = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'roberta-base','roberta',  1, 32, 64)
  print('Roberta')
  print('ACC:' + str(roberta[0]))
  print('F1:' + str(roberta[1]))

  # cnn_acc.append(svm[0])
  # cnn_f1.append(svm[1])

  # lstm_acc.append(lstm[0])
  # lstm_f1.append(lstm[1])

  bert_acc.append(bert[0])
  bert_f1.append(bert[1])

  xlnet_acc.append(xlnet[0])
  xlnet_f1.append(xlnet[1])

  roberta_acc.append(roberta[0])
  roberta_f1.append(roberta[1])

0


<ipython-input-10-a91fedf45f9b>:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  fim = original.append(parafrase)
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:612: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/864 [00:00<?, ?it/s]

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/27 [00:00<?, ?it/s]

...

Running Epoch 0 of 1:   0%|          | 0/27 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1454: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/784 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/98 [00:00<?, ?it/s]

Roberta
ACC:0.6045918367346939
F1:0.6031040969899666


In [ ]:
data = {'Aug': [ 'original1', 'original2', 'original3', 'original4','original5'],
      #  'CNN_ACC': cnn_acc, 'CNN_F1':cnn_f1,
      #   'LSTM_ACC': lstm_acc, 'LSTM_F1':lstm_f1,
        'BERT_ACC': bert_acc, 'BERT_F1':bert_f1,
        'XLNET_ACC': xlnet_acc, 'XLNET_F1':xlnet_f1,
        'ROBERTA_ACC': roberta_acc, 'ROBERTA_F1':roberta_f1,}



base_resultados = pd.DataFrame.from_dict(data)

In [ ]:
base_resultados

Aug  BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
0  original1  0.567602  0.561697   0.505102  0.501988     0.521684    0.521403
1  original2  0.673469  0.671795   0.542092  0.487918     0.566327    0.566098
2  original3  0.463010  0.414812   0.534439  0.533886     0.410714    0.315804
3  original4  0.603316  0.577158   0.501276  0.490695     0.602041    0.600000
4  original5  0.590561  0.437465   0.565051  0.560358     0.604592    0.603104

In [ ]:
base_resultados.describe()

BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
count  5.000000  5.000000   5.000000  5.000000     5.000000    5.000000
mean   0.579592  0.532585   0.529592  0.514969     0.541071    0.521282
std    0.076209  0.106221   0.026640  0.031255     0.080248    0.119500
min    0.463010  0.414812   0.501276  0.487918     0.410714    0.315804
25%    0.567602  0.437465   0.505102  0.490695     0.521684    0.521403
50%    0.590561  0.561697   0.534439  0.501988     0.566327    0.566098
75%    0.603316  0.577158   0.542092  0.533886     0.602041    0.600000
max    0.673469  0.671795   0.565051  0.560358     0.604592    0.603104

# Checklist

In [ ]:
perc = 5
i=0
from tensorflow.keras import regularizers
from tensorflow.keras.constraints import MaxNorm
arqs = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/checklist/base_ironic_'+str(perc)+'_checklist'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/checklist/base_ironic_'+str(perc)+'_checklist'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/checklist/base_ironic_'+str(perc)+'_checklist'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/checklist/base_ironic_'+str(perc)+'_checklist'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/checklist/base_ironic_'+str(perc)+'_checklist'+str(i+5)+'.csv',
       ]

cnn_acc = []
cnn_f1 = []
lstm_acc = []
lstm_f1 = []
bert_acc = []
bert_f1 = []
xlnet_acc = []
xlnet_f1 = []
roberta_acc = []
roberta_f1 = []
import gc
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
torch.cuda.empty_cache()
gc.collect()
for j in range(len(arqs)):
  print(j)
  X_train,  y_train = puxa_dados_normal(arqs[j])
  # svm = desempenho_CNN(X_train,  X_test, y_train,  y_test, nclasses, 15)
  # print('CNN')
  # print('ACC:' + str(svm[0]))
  # print('F1:' + str(svm[1]))
  # lstm = desempenho_LSTM(X_train,  X_test, y_train,  y_test, nclasses, 5)
  # print('LSTM')
  # print('ACC:' + str(lstm[0]))
  # print('F1:' + str(lstm[1]))
  # torch.cuda.empty_cache()
  # gc.collect()
  bert = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'bert-base-uncased','bert', 4, 32, 64)

  print('BERT')
  print('ACC:' + str(bert[0]))
  print('F1:' + str(bert[1]))

  torch.cuda.empty_cache()
  gc.collect()

  xlnet = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'xlnet-base-cased','xlnet',  4, 32, 64)
  print('XlNet')
  print('ACC:' + str(xlnet[0]))
  print('F1:' + str(xlnet[1]))

  torch.cuda.empty_cache()
  gc.collect()

  roberta = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'roberta-base','roberta',  4, 32, 64)
  print('Roberta')
  print('ACC:' + str(roberta[0]))
  print('F1:' + str(roberta[1]))

  # cnn_acc.append(svm[0])
  # cnn_f1.append(svm[1])

  # lstm_acc.append(lstm[0])
  # lstm_f1.append(lstm[1])

  bert_acc.append(bert[0])
  bert_f1.append(bert[1])

  xlnet_acc.append(xlnet[0])
  xlnet_f1.append(xlnet[1])

  roberta_acc.append(roberta[0])
  roberta_f1.append(roberta[1])

0


<ipython-input-10-a91fedf45f9b>:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  fim = original.append(parafrase)
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:612: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/482 [00:00<?, ?it/s]

Epoch:   0%|          | 0/4 [00:00<?, ?it/s]

Running Epoch 0 of 4:   0%|          | 0/16 [00:00<?, ?it/s]

...

Running Epoch 3 of 4:   0%|          | 0/14 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1454: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/784 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/98 [00:00<?, ?it/s]

Roberta
ACC:0.6160714285714286
F1:0.6146866586006625


In [ ]:
data = {'Aug': [ 'original1', 'original2', 'original3', 'original4','original5'],
      #  'CNN_ACC': cnn_acc, 'CNN_F1':cnn_f1,
      #   'LSTM_ACC': lstm_acc, 'LSTM_F1':lstm_f1,
        'BERT_ACC': bert_acc, 'BERT_F1':bert_f1,
        'XLNET_ACC': xlnet_acc, 'XLNET_F1':xlnet_f1,
        'ROBERTA_ACC': roberta_acc, 'ROBERTA_F1':roberta_f1,}



base_resultados = pd.DataFrame.from_dict(data)

In [ ]:
base_resultados

Aug  BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
0  original1  0.635204  0.635119   0.617347  0.612903     0.575255    0.547854
1  original2  0.664541  0.658174   0.633929  0.630727     0.646684    0.645182
2  original3  0.566327  0.561290   0.616071  0.599168     0.577806    0.575062
3  original4  0.628827  0.627906   0.593112  0.546644     0.641582    0.638618
4  original5  0.585459  0.584967   0.567602  0.567568     0.616071    0.614687

In [ ]:
base_resultados.describe()

BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
count  5.000000  5.000000   5.000000  5.000000     5.000000    5.000000
mean   0.616071  0.613491   0.605612  0.591402     0.611480    0.604281
std    0.039654  0.039404   0.025739  0.034060     0.033958    0.041827
min    0.566327  0.561290   0.567602  0.546644     0.575255    0.547854
25%    0.585459  0.584967   0.593112  0.567568     0.577806    0.575062
50%    0.628827  0.627906   0.616071  0.599168     0.616071    0.614687
75%    0.635204  0.635119   0.617347  0.612903     0.641582    0.638618
max    0.664541  0.658174   0.633929  0.630727     0.646684    0.645182

# Back Translation

In [ ]:
perc = 5
i=0
from tensorflow.keras import regularizers
from tensorflow.keras.constraints import MaxNorm
arqs = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/back_translation/base_ironic_'+str(perc)+'_back_translation'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/back_translation/base_ironic_'+str(perc)+'_back_translation'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/back_translation/base_ironic_'+str(perc)+'_back_translation'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/back_translation/base_ironic_'+str(perc)+'_back_translation'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/back_translation/base_ironic_'+str(perc)+'_back_translation'+str(i+5)+'.csv',
       ]

cnn_acc = []
cnn_f1 = []
lstm_acc = []
lstm_f1 = []
bert_acc = []
bert_f1 = []
xlnet_acc = []
xlnet_f1 = []
roberta_acc = []
roberta_f1 = []
import gc
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
torch.cuda.empty_cache()
gc.collect()
for j in range(len(arqs)):
  print(j)
  X_train,  y_train = puxa_dados_normal(arqs[j])
  # svm = desempenho_CNN(X_train,  X_test, y_train,  y_test, nclasses, 15)
  # print('CNN')
  # print('ACC:' + str(svm[0]))
  # print('F1:' + str(svm[1]))
  # lstm = desempenho_LSTM(X_train,  X_test, y_train,  y_test, nclasses, 5)
  # print('LSTM')
  # print('ACC:' + str(lstm[0]))
  # print('F1:' + str(lstm[1]))
  # torch.cuda.empty_cache()
  # gc.collect()
  bert = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'bert-base-uncased','bert', 4, 32, 64)

  print('BERT')
  print('ACC:' + str(bert[0]))
  print('F1:' + str(bert[1]))

  torch.cuda.empty_cache()
  gc.collect()

  xlnet = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'xlnet-base-cased','xlnet',  4, 32, 64)
  print('XlNet')
  print('ACC:' + str(xlnet[0]))
  print('F1:' + str(xlnet[1]))

  torch.cuda.empty_cache()
  gc.collect()

  roberta = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'roberta-base','roberta',  4, 32, 64)
  print('Roberta')
  print('ACC:' + str(roberta[0]))
  print('F1:' + str(roberta[1]))

  # cnn_acc.append(svm[0])
  # cnn_f1.append(svm[1])

  # lstm_acc.append(lstm[0])
  # lstm_f1.append(lstm[1])

  bert_acc.append(bert[0])
  bert_f1.append(bert[1])

  xlnet_acc.append(xlnet[0])
  xlnet_f1.append(xlnet[1])

  roberta_acc.append(roberta[0])
  roberta_f1.append(roberta[1])

0


<ipython-input-10-a91fedf45f9b>:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  fim = original.append(parafrase)
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:612: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/288 [00:00<?, ?it/s]

Epoch:   0%|          | 0/4 [00:00<?, ?it/s]

Running Epoch 0 of 4:   0%|          | 0/9 [00:00<?, ?it/s]

...

Running Epoch 3 of 4:   0%|          | 0/9 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1454: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/784 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/98 [00:00<?, ?it/s]

Roberta
ACC:0.6301020408163265
F1:0.6247070086824469


In [ ]:
data = {'Aug': [ 'original1', 'original2', 'original3', 'original4','original5'],
      #  'CNN_ACC': cnn_acc, 'CNN_F1':cnn_f1,
      #   'LSTM_ACC': lstm_acc, 'LSTM_F1':lstm_f1,
        'BERT_ACC': bert_acc, 'BERT_F1':bert_f1,
        'XLNET_ACC': xlnet_acc, 'XLNET_F1':xlnet_f1,
        'ROBERTA_ACC': roberta_acc, 'ROBERTA_F1':roberta_f1,}



base_resultados = pd.DataFrame.from_dict(data)

In [ ]:
base_resultados

Aug  BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
0  original1  0.614796  0.610104   0.540816  0.527834     0.510204    0.462304
1  original2  0.572704  0.572503   0.625000  0.618798     0.599490    0.579729
2  original3  0.563776  0.543814   0.575255  0.572668     0.536990    0.532713
3  original4  0.575255  0.481760   0.567602  0.549538     0.580357    0.504357
4  original5  0.545918  0.524606   0.580357  0.580203     0.630102    0.624707

In [ ]:
base_resultados.describe()

BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
count  5.000000  5.000000   5.000000  5.000000     5.000000    5.000000
mean   0.574490  0.546557   0.577806  0.569808     0.571429    0.540762
std    0.025296  0.048475   0.030466  0.034238     0.048073    0.063465
min    0.545918  0.481760   0.540816  0.527834     0.510204    0.462304
25%    0.563776  0.524606   0.567602  0.549538     0.536990    0.504357
50%    0.572704  0.543814   0.575255  0.572668     0.580357    0.532713
75%    0.575255  0.572503   0.580357  0.580203     0.599490    0.579729
max    0.614796  0.610104   0.625000  0.618798     0.630102    0.624707

# LAMBADA

In [ ]:
perc = 5
i=0
from tensorflow.keras import regularizers
from tensorflow.keras.constraints import MaxNorm
arqs = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/lambada/base_ironic_'+str(perc)+'_lambada'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/lambada/base_ironic_'+str(perc)+'_lambada'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/lambada/base_ironic_'+str(perc)+'_lambada'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/lambada/base_ironic_'+str(perc)+'_lambada'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/lambada/base_ironic_'+str(perc)+'_lambada'+str(i+5)+'.csv',
       ]
borig = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/base_ironic_'+str(perc)+'_original'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/base_ironic_'+str(perc)+'_original'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/base_ironic_'+str(perc)+'_original'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/base_ironic_'+str(perc)+'_original'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/base_ironic_'+str(perc)+'_original'+str(i+5)+'.csv',
       ]

cnn_acc = []
cnn_f1 = []
lstm_acc = []
lstm_f1 = []
bert_acc = []
bert_f1 = []
xlnet_acc = []
xlnet_f1 = []
roberta_acc = []
roberta_f1 = []
import gc
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
torch.cuda.empty_cache()
gc.collect()
for j in range(len(arqs)):
  print(j)
  X_train,  y_train = puxa_dados_lambada(arqs[j], borig[j])
  # svm = desempenho_CNN(X_train,  X_test, y_train,  y_test, nclasses, 15)
  # print('CNN')
  # print('ACC:' + str(svm[0]))
  # print('F1:' + str(svm[1]))
  # lstm = desempenho_LSTM(X_train,  X_test, y_train,  y_test, nclasses, 5)
  # print('LSTM')
  # print('ACC:' + str(lstm[0]))
  # print('F1:' + str(lstm[1]))
  # torch.cuda.empty_cache()
  # gc.collect()
  bert = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'bert-base-uncased','bert', 1, 32, 64)

  print('BERT')
  print('ACC:' + str(bert[0]))
  print('F1:' + str(bert[1]))

  torch.cuda.empty_cache()
  gc.collect()

  xlnet = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'xlnet-base-cased','xlnet',  1, 32, 64)
  print('XlNet')
  print('ACC:' + str(xlnet[0]))
  print('F1:' + str(xlnet[1]))

  torch.cuda.empty_cache()
  gc.collect()

  roberta = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'roberta-base','roberta',  1, 32, 64)
  print('Roberta')
  print('ACC:' + str(roberta[0]))
  print('F1:' + str(roberta[1]))

  # cnn_acc.append(svm[0])
  # cnn_f1.append(svm[1])

  # lstm_acc.append(lstm[0])
  # lstm_f1.append(lstm[1])

  bert_acc.append(bert[0])
  bert_f1.append(bert[1])

  xlnet_acc.append(xlnet[0])
  xlnet_f1.append(xlnet[1])

  roberta_acc.append(roberta[0])
  roberta_f1.append(roberta[1])

0


<ipython-input-12-df95bd675bd6>:13: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  fim = original.append(parafrase)
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:612: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/144 [00:00<?, ?it/s]

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/5 [00:00<?, ?it/s]

...

Running Epoch 0 of 1:   0%|          | 0/27 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1454: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/784 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/98 [00:00<?, ?it/s]

Roberta
ACC:0.39668367346938777
F1:0.28401826484018267


In [ ]:
data = {'Aug': [ 'original1', 'original2', 'original3', 'original4','original5'],
      #  'CNN_ACC': cnn_acc, 'CNN_F1':cnn_f1,
      #   'LSTM_ACC': lstm_acc, 'LSTM_F1':lstm_f1,
        'BERT_ACC': bert_acc, 'BERT_F1':bert_f1,
        'XLNET_ACC': xlnet_acc, 'XLNET_F1':xlnet_f1,
        'ROBERTA_ACC': roberta_acc, 'ROBERTA_F1':roberta_f1,}



base_resultados = pd.DataFrame.from_dict(data)

In [ ]:
base_resultados

Aug  BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
0  original1  0.568878  0.390655   0.605867  0.448283     0.603316    0.376293
1  original2  0.598214  0.566839   0.545918  0.544849     0.544643    0.473038
2  original3  0.512755  0.365185   0.575255  0.386335     0.603316    0.376293
3  original4  0.562500  0.439728   0.570153  0.492305     0.603316    0.376293
4  original5  0.396684  0.284018   0.396684  0.284018     0.396684    0.284018

In [ ]:
base_resultados.describe()

BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
count  5.000000  5.000000   5.000000  5.000000     5.000000    5.000000
mean   0.527806  0.409285   0.538776  0.431158     0.550255    0.377187
std    0.079479  0.104563   0.082246  0.100768     0.089530    0.066840
min    0.396684  0.284018   0.396684  0.284018     0.396684    0.284018
25%    0.512755  0.365185   0.545918  0.386335     0.544643    0.376293
50%    0.562500  0.390655   0.570153  0.448283     0.603316    0.376293
75%    0.568878  0.439728   0.575255  0.492305     0.603316    0.376293
max    0.598214  0.566839   0.605867  0.544849     0.603316    0.473038

# Contrastive LAMBADA

In [ ]:
perc = 5
i=0
from tensorflow.keras import regularizers
from tensorflow.keras.constraints import MaxNorm
arqs = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/lambada/base_ironic_'+str(perc)+'_lambada_contrastive'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/lambada/base_ironic_'+str(perc)+'_lambada_contrastive'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/lambada/base_ironic_'+str(perc)+'_lambada_contrastive'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/lambada/base_ironic_'+str(perc)+'_lambada_contrastive'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/lambada/base_ironic_'+str(perc)+'_lambada_contrastive'+str(i+5)+'.csv',
       ]
borig = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/base_ironic_'+str(perc)+'_original'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/base_ironic_'+str(perc)+'_original'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/base_ironic_'+str(perc)+'_original'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/base_ironic_'+str(perc)+'_original'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/base_ironic_'+str(perc)+'_original'+str(i+5)+'.csv',
       ]

cnn_acc = []
cnn_f1 = []
lstm_acc = []
lstm_f1 = []
bert_acc = []
bert_f1 = []
xlnet_acc = []
xlnet_f1 = []
roberta_acc = []
roberta_f1 = []
import gc
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
torch.cuda.empty_cache()
gc.collect()
for j in range(len(arqs)):
  print(j)
  X_train,  y_train = puxa_dados_lambada(arqs[j], borig[j])
  # svm = desempenho_CNN(X_train,  X_test, y_train,  y_test, nclasses, 15)
  # print('CNN')
  # print('ACC:' + str(svm[0]))
  # print('F1:' + str(svm[1]))
  # lstm = desempenho_LSTM(X_train,  X_test, y_train,  y_test, nclasses, 5)
  # print('LSTM')
  # print('ACC:' + str(lstm[0]))
  # print('F1:' + str(lstm[1]))
  # torch.cuda.empty_cache()
  gc.collect()
  bert = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'bert-base-uncased','bert', 1, 32, 64)

  print('BERT')
  print('ACC:' + str(bert[0]))
  print('F1:' + str(bert[1]))

  torch.cuda.empty_cache()
  gc.collect()

  xlnet = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'xlnet-base-cased','xlnet',  1, 32, 64)
  print('XlNet')
  print('ACC:' + str(xlnet[0]))
  print('F1:' + str(xlnet[1]))

  torch.cuda.empty_cache()
  gc.collect()

  roberta = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'roberta-base','roberta',  1, 32, 64)
  print('Roberta')
  print('ACC:' + str(roberta[0]))
  print('F1:' + str(roberta[1]))

  # cnn_acc.append(svm[0])
  # cnn_f1.append(svm[1])

  # lstm_acc.append(lstm[0])
  # lstm_f1.append(lstm[1])

  bert_acc.append(bert[0])
  bert_f1.append(bert[1])

  xlnet_acc.append(xlnet[0])
  xlnet_f1.append(xlnet[1])

  roberta_acc.append(roberta[0])
  roberta_f1.append(roberta[1])

0


<ipython-input-12-df95bd675bd6>:13: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  fim = original.append(parafrase)
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:612: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/864 [00:00<?, ?it/s]

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/27 [00:00<?, ?it/s]

...

Running Epoch 0 of 1:   0%|          | 0/27 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1454: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/784 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/98 [00:00<?, ?it/s]

Roberta
ACC:0.5586734693877551
F1:0.3762325239146431


In [ ]:
data = {'Aug': [ 'original1', 'original2', 'original3', 'original4','original5'],
      #  'CNN_ACC': cnn_acc, 'CNN_F1':cnn_f1,
      #   'LSTM_ACC': lstm_acc, 'LSTM_F1':lstm_f1,
        'BERT_ACC': bert_acc, 'BERT_F1':bert_f1,
        'XLNET_ACC': xlnet_acc, 'XLNET_F1':xlnet_f1,
        'ROBERTA_ACC': roberta_acc, 'ROBERTA_F1':roberta_f1,}



base_resultados = pd.DataFrame.from_dict(data)

In [ ]:
base_resultados

Aug  BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
0  original1  0.535714  0.531310   0.584184  0.583098     0.522959    0.521586
1  original2  0.605867  0.578726   0.571429  0.535516     0.492347    0.356709
2  original3  0.396684  0.284018   0.454082  0.395532     0.396684    0.284018
3  original4  0.508929  0.503891   0.494898  0.491719     0.396684    0.284018
4  original5  0.497449  0.402883   0.600765  0.570223     0.558673    0.376233

In [ ]:
base_resultados.describe()

BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
count  5.000000  5.000000   5.000000  5.000000     5.000000    5.000000
mean   0.508929  0.460166   0.541071  0.515218     0.473469    0.364513
std    0.075573  0.117621   0.063330  0.075700     0.073921    0.097248
min    0.396684  0.284018   0.454082  0.395532     0.396684    0.284018
25%    0.497449  0.402883   0.494898  0.491719     0.396684    0.284018
50%    0.508929  0.503891   0.571429  0.535516     0.492347    0.356709
75%    0.535714  0.531310   0.584184  0.570223     0.522959    0.376233
max    0.605867  0.578726   0.600765  0.583098     0.558673    0.521586

# LLAMA 2 Paraphraser

In [ ]:
perc = 5
i=0
from tensorflow.keras import regularizers
from tensorflow.keras.constraints import MaxNorm
arqs = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/gptparaphrase/base_ironic_'+str(perc)+'_gptparaphrase'+str(i+1)+'.pkl',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/gptparaphrase/base_ironic_'+str(perc)+'_gptparaphrase'+str(i+2)+'.pkl',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/gptparaphrase/base_ironic_'+str(perc)+'_gptparaphrase'+str(i+3)+'.pkl',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/gptparaphrase/base_ironic_'+str(perc)+'_gptparaphrase'+str(i+4)+'.pkl',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/gptparaphrase/base_ironic_'+str(perc)+'_gptparaphrase'+str(i+5)+'.pkl',
       ]

cnn_acc = []
cnn_f1 = []
lstm_acc = []
lstm_f1 = []
bert_acc = []
bert_f1 = []
xlnet_acc = []
xlnet_f1 = []
roberta_acc = []
roberta_f1 = []
import gc
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
torch.cuda.empty_cache()
gc.collect()
for j in range(len(arqs)):
  print(j)
  X_train,  y_train = puxa_dados_normal_pkl(arqs[j])
  # svm = desempenho_CNN(X_train,  X_test, y_train,  y_test, nclasses, 15)
  # print('CNN')
  # print('ACC:' + str(svm[0]))
  # print('F1:' + str(svm[1]))
  # lstm = desempenho_LSTM(X_train,  X_test, y_train,  y_test, nclasses, 5)
  # print('LSTM')
  # print('ACC:' + str(lstm[0]))
  # print('F1:' + str(lstm[1]))
  # torch.cuda.empty_cache()
  # gc.collect()
  bert = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'bert-base-uncased','bert', 4, 32, 64)

  print('BERT')
  print('ACC:' + str(bert[0]))
  print('F1:' + str(bert[1]))

  torch.cuda.empty_cache()
  gc.collect()

  xlnet = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'xlnet-base-cased','xlnet', 4, 32, 64)
  print('XlNet')
  print('ACC:' + str(xlnet[0]))
  print('F1:' + str(xlnet[1]))

  torch.cuda.empty_cache()
  gc.collect()

  roberta = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'roberta-base','roberta',  4, 32, 64)
  print('Roberta')
  print('ACC:' + str(roberta[0]))
  print('F1:' + str(roberta[1]))

  # cnn_acc.append(svm[0])
  # cnn_f1.append(svm[1])

  # lstm_acc.append(lstm[0])
  # lstm_f1.append(lstm[1])

  bert_acc.append(bert[0])
  bert_f1.append(bert[1])

  xlnet_acc.append(xlnet[0])
  xlnet_f1.append(xlnet[1])

  roberta_acc.append(roberta[0])
  roberta_f1.append(roberta[1])

0


<ipython-input-13-8a66c1fcd9f8>:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  fim = original.append(parafrase)
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:612: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/840 [00:00<?, ?it/s]

Epoch:   0%|          | 0/4 [00:00<?, ?it/s]

Running Epoch 0 of 4:   0%|          | 0/27 [00:00<?, ?it/s]

...

Running Epoch 3 of 4:   0%|          | 0/27 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1454: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/784 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/98 [00:00<?, ?it/s]

Roberta
ACC:0.6403061224489796
F1:0.6403037816520569


In [ ]:
data = {'Aug': [ 'original1', 'original2', 'original3', 'original4','original5'],
      #  'CNN_ACC': cnn_acc, 'CNN_F1':cnn_f1,
      #   'LSTM_ACC': lstm_acc, 'LSTM_F1':lstm_f1,
        'BERT_ACC': bert_acc, 'BERT_F1':bert_f1,
        'XLNET_ACC': xlnet_acc, 'XLNET_F1':xlnet_f1,
        'ROBERTA_ACC': roberta_acc, 'ROBERTA_F1':roberta_f1,}



base_resultados = pd.DataFrame.from_dict(data)

In [ ]:
base_resultados

Aug  BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
0  original1  0.571429  0.515676   0.630102  0.630042     0.554847    0.528599
1  original2  0.613520  0.602068   0.650510  0.647016     0.639031    0.632438
2  original3  0.623724  0.617116   0.654337  0.643119     0.661990    0.660194
3  original4  0.632653  0.626822   0.617347  0.599837     0.632653    0.632536
4  original5  0.605867  0.599481   0.609694  0.609264     0.640306    0.640304

In [ ]:
base_resultados.describe()

BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
count  5.000000  5.000000   5.000000  5.000000     5.000000    5.000000
mean   0.609439  0.592233   0.632398  0.625856     0.625765    0.618814
std    0.023543  0.044232   0.019727  0.020710     0.041160    0.051688
min    0.571429  0.515676   0.609694  0.599837     0.554847    0.528599
25%    0.605867  0.599481   0.617347  0.609264     0.632653    0.632438
50%    0.613520  0.602068   0.630102  0.630042     0.639031    0.632536
75%    0.623724  0.617116   0.650510  0.643119     0.640306    0.640304
max    0.632653  0.626822   0.654337  0.647016     0.661990    0.660194

# ProtAugment

In [27]:
perc = 5
i=0
from tensorflow.keras import regularizers
from tensorflow.keras.constraints import MaxNorm
arqs = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/protaugment/base_ironic_'+str(perc)+'_protaugment'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/protaugment/base_ironic_'+str(perc)+'_protaugment'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/protaugment/base_ironic_'+str(perc)+'_protaugment'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/protaugment/base_ironic_'+str(perc)+'_protaugment'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/protaugment/base_ironic_'+str(perc)+'_protaugment'+str(i+5)+'.csv',
       ]

cnn_acc = []
cnn_f1 = []
lstm_acc = []
lstm_f1 = []
bert_acc = []
bert_f1 = []
xlnet_acc = []
xlnet_f1 = []
roberta_acc = []
roberta_f1 = []
import gc
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
torch.cuda.empty_cache()
gc.collect()
for j in range(len(arqs)):
  print(j)
  X_train,  y_train = puxa_dados_normal(arqs[j])
  # svm = desempenho_CNN(X_train,  X_test, y_train,  y_test, nclasses, 15)
  # print('CNN')
  # print('ACC:' + str(svm[0]))
  # print('F1:' + str(svm[1]))
  # lstm = desempenho_LSTM(X_train,  X_test, y_train,  y_test, nclasses, 5)
  # print('LSTM')
  # print('ACC:' + str(lstm[0]))
  # print('F1:' + str(lstm[1]))
  # torch.cuda.empty_cache()
  # gc.collect()
  bert = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'bert-base-uncased','bert', 4, 32, 64)

  print('BERT')
  print('ACC:' + str(bert[0]))
  print('F1:' + str(bert[1]))

  torch.cuda.empty_cache()
  gc.collect()

  xlnet = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'xlnet-base-cased','xlnet', 4, 32, 64)
  print('XlNet')
  print('ACC:' + str(xlnet[0]))
  print('F1:' + str(xlnet[1]))

  torch.cuda.empty_cache()
  gc.collect()

  roberta = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'roberta-base','roberta',  4, 32, 64)
  print('Roberta')
  print('ACC:' + str(roberta[0]))
  print('F1:' + str(roberta[1]))

  # cnn_acc.append(svm[0])
  # cnn_f1.append(svm[1])

  # lstm_acc.append(lstm[0])
  # lstm_f1.append(lstm[1])

  bert_acc.append(bert[0])
  bert_f1.append(bert[1])

  xlnet_acc.append(xlnet[0])
  xlnet_f1.append(xlnet[1])

  roberta_acc.append(roberta[0])
  roberta_f1.append(roberta[1])

0


<ipython-input-10-a91fedf45f9b>:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  fim = original.append(parafrase)
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:612: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/822 [00:00<?, ?it/s]

Epoch:   0%|          | 0/4 [00:00<?, ?it/s]

Running Epoch 0 of 4:   0%|          | 0/26 [00:00<?, ?it/s]

...

Running Epoch 3 of 4:   0%|          | 0/26 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1454: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/784 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/98 [00:00<?, ?it/s]

Roberta
ACC:0.6632653061224489
F1:0.6554603383871677


In [28]:
data = {'Aug': [ 'eda1', 'eda2', 'eda3', 'eda4','eda5'],
      #  'CNN_ACC': cnn_acc, 'CNN_F1':cnn_f1,
      #   'LSTM_ACC': lstm_acc, 'LSTM_F1':lstm_f1,
        'BERT_ACC': bert_acc, 'BERT_F1':bert_f1,
        'XLNET_ACC': xlnet_acc, 'XLNET_F1':xlnet_f1,
        'ROBERTA_ACC': roberta_acc, 'ROBERTA_F1':roberta_f1,}



base_resultados = pd.DataFrame.from_dict(data)

In [29]:
base_resultados.describe()

BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
count  5.000000  5.000000   5.000000  5.000000     5.000000    5.000000
mean   0.613520  0.611006   0.618878  0.612575     0.639031    0.635533
std    0.038971  0.037320   0.035685  0.039213     0.013826    0.011526
min    0.552296  0.552278   0.573980  0.557341     0.628827    0.626713
25%    0.599490  0.599323   0.593112  0.592820     0.632653    0.628811
50%    0.628827  0.620952   0.625000  0.624961     0.633929    0.632414
75%    0.636480  0.635834   0.639031  0.626608     0.636480    0.634266
max    0.650510  0.646645   0.663265  0.661146     0.663265    0.655460

# GPTNEOKEY

In [30]:
perc = 5
i=0
from tensorflow.keras import regularizers
from tensorflow.keras.constraints import MaxNorm
arqs = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/teste_algo/base_ironic_'+str(perc)+'_gptneokey'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/teste_algo/base_ironic_'+str(perc)+'_gptneokey'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/teste_algo/base_ironic_'+str(perc)+'_gptneokey'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/teste_algo/base_ironic_'+str(perc)+'_gptneokey'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/teste_algo/base_ironic_'+str(perc)+'_gptneokey'+str(i+5)+'.csv',
       ]
borig = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/base_ironic_'+str(perc)+'_original'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/base_ironic_'+str(perc)+'_original'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/base_ironic_'+str(perc)+'_original'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/base_ironic_'+str(perc)+'_original'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/ironic/base_ironic_'+str(perc)+'_original'+str(i+5)+'.csv',
       ]

cnn_acc = []
cnn_f1 = []
lstm_acc = []
lstm_f1 = []
bert_acc = []
bert_f1 = []
xlnet_acc = []
xlnet_f1 = []
roberta_acc = []
roberta_f1 = []
import gc
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
torch.cuda.empty_cache()
gc.collect()
for j in range(len(arqs)):
  print(j)
  X_train,  y_train = puxa_dados_lambada(arqs[j], borig[j])
  # svm = desempenho_CNN(X_train,  X_test, y_train,  y_test, nclasses, 15)
  # print('CNN')
  # print('ACC:' + str(svm[0]))
  # print('F1:' + str(svm[1]))
  # lstm = desempenho_LSTM(X_train,  X_test, y_train,  y_test, nclasses, 5)
  # print('LSTM')
  # print('ACC:' + str(lstm[0]))
  # print('F1:' + str(lstm[1]))
  # torch.cuda.empty_cache()
  # gc.collect()
  bert = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'bert-base-uncased','bert', 4, 32, 64)

  print('BERT')
  print('ACC:' + str(bert[0]))
  print('F1:' + str(bert[1]))

  torch.cuda.empty_cache()
  gc.collect()

  xlnet = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'xlnet-base-cased','xlnet',  4, 32, 64)
  print('XlNet')
  print('ACC:' + str(xlnet[0]))
  print('F1:' + str(xlnet[1]))

  torch.cuda.empty_cache()
  gc.collect()

  roberta = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'roberta-base','roberta',  4, 32, 64)
  print('Roberta')
  print('ACC:' + str(roberta[0]))
  print('F1:' + str(roberta[1]))

  # cnn_acc.append(svm[0])
  # cnn_f1.append(svm[1])

  # lstm_acc.append(lstm[0])
  # lstm_f1.append(lstm[1])

  bert_acc.append(bert[0])
  bert_f1.append(bert[1])

  xlnet_acc.append(xlnet[0])
  xlnet_f1.append(xlnet[1])

  roberta_acc.append(roberta[0])
  roberta_f1.append(roberta[1])

0


<ipython-input-12-df95bd675bd6>:13: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  fim = original.append(parafrase)
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:612: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/864 [00:00<?, ?it/s]

Epoch:   0%|          | 0/4 [00:00<?, ?it/s]

Running Epoch 0 of 4:   0%|          | 0/27 [00:00<?, ?it/s]

...

Running Epoch 3 of 4:   0%|          | 0/27 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1454: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/784 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/98 [00:00<?, ?it/s]

Roberta
ACC:0.5918367346938775
F1:0.5908755862572813


In [31]:
data = {'Aug': [ 'eda1', 'eda2', 'eda3', 'eda4','eda5'], # 'eda1', 'eda2', 'eda3', 'eda4','eda5'],
      #  'CNN_ACC': cnn_acc, 'CNN_F1':cnn_f1,
      #   'LSTM_ACC': lstm_acc, 'LSTM_F1':lstm_f1,
        'BERT_ACC': bert_acc, 'BERT_F1':bert_f1,
        'XLNET_ACC': xlnet_acc, 'XLNET_F1':xlnet_f1,
        'ROBERTA_ACC': roberta_acc, 'ROBERTA_F1':roberta_f1,}



base_resultados = pd.DataFrame.from_dict(data)

In [32]:
base_resultados

Aug  BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
0  eda1  0.594388  0.587680   0.580357  0.576687     0.593112    0.582499
1  eda2  0.577806  0.566429   0.622449  0.620371     0.609694    0.607546
2  eda3  0.594388  0.593941   0.591837  0.587097     0.661990    0.659793
3  eda4  0.599490  0.594141   0.616071  0.614687     0.591837    0.582376
4  eda5  0.557398  0.548674   0.581633  0.581458     0.591837    0.590876

In [33]:
base_resultados.describe()

BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
count  5.000000  5.000000   5.000000  5.000000     5.000000    5.000000
mean   0.584694  0.578173   0.598469  0.596060     0.609694    0.604618
std    0.017316  0.020013   0.019624  0.020043     0.030198    0.032503
min    0.557398  0.548674   0.580357  0.576687     0.591837    0.582376
25%    0.577806  0.566429   0.581633  0.581458     0.591837    0.582499
50%    0.594388  0.587680   0.591837  0.587097     0.593112    0.590876
75%    0.594388  0.593941   0.616071  0.614687     0.609694    0.607546
max    0.599490  0.594141   0.622449  0.620371     0.661990    0.659793